In [12]:
import xml.etree.ElementTree as ET
import pandas as pd
import os

In [13]:
def classify_app_from_manifest(manifest_file):
    try:
        # Đọc và phân tích file manifest
        tree = ET.parse(manifest_file)
        root = tree.getroot()

        # Kiểm tra sự tồn tại của thư viện Wear OS
        wearable_library_present = False
        wearable_library_required = False
        standalone_metadata_present = False
        standalone_metadata_value = None
        
        # Danh sách lưu trữ bằng chứng
        evidence = []
        
        # Duyệt qua các phần tử <uses-library> và <meta-data>
        for elem in root.findall("uses-library"):
            if elem.get("android:name") == "com.google.android.wearable":
                wearable_library_present = True
                evidence.append("Found <uses-library> with com.google.android.wearable")
                # Kiểm tra thuộc tính required
                if elem.get("android:required") == "true":
                    wearable_library_required = True
                    evidence.append("Found required='true' in <uses-library>")
                else:
                    evidence.append("Found required='false' in <uses-library>")

        # Kiểm tra thẻ <meta-data> để xác định standalone app
        for elem in root.findall("application/meta-data"):
            if elem.get("android:name") == "com.google.android.wearable.standalone":
                standalone_metadata_present = True
                standalone_metadata_value = elem.get("android:value")
                evidence.append(f"Found <meta-data> com.google.android.wearable.standalone with value={standalone_metadata_value}")

        # Điều kiện phân loại
        if not wearable_library_present:
            evidence.append("No <uses-library> for com.google.android.wearable found")
            return ["Companion App", evidence]
        elif wearable_library_present and wearable_library_required:
            if standalone_metadata_present and standalone_metadata_value == "true":
                return ["Standalone App", evidence]
            elif standalone_metadata_present and standalone_metadata_value == "false":
                return ["Embedded App", evidence]
            else:
                evidence.append("No standalone metadata found or metadata value is neither true nor false")
                return ["Embedded App", evidence]
        else:
            return ["Companion App", evidence]
    except ET.ParseError:
        return ["Invalid Manifest file", ["Error parsing the manifest file"]]
def read_csv_and_filter(file_path):
    # Read the CSV file into a pandas DataFrame
    df = pd.read_csv(file_path)

    # Filter rows where the 'manifest' column has a NaN value
    filtered_df = df[df['app_group'].isna()]

    # Extract the 'apkfile_name' column from the filtered DataFrame
    apkfile_names = filtered_df['apkfile_name_new'].tolist()
    pkg_names = filtered_df['pkg_name'].tolist()
    return apkfile_names, pkg_names
# Funtion update CSV data
def update_csv_column(csv_path, condition_column, condition_value, update_column, new_value):
    # Read the CSV file into a DataFrame
    df = pd.read_csv(csv_path)
    
    # Ensure the update_column is of type object (can hold strings)
    df[update_column] = df[update_column].astype(object)

    # Print the matching rows (for debugging purposes)
    print(f"Checking for rows where {condition_column} == {condition_value}")
    matching_rows = df.loc[df[condition_column] == condition_value]
    print(f"Found {len(matching_rows)} matching rows")

    # Update the specified column based on the condition
    if len(matching_rows) > 0:
        df.loc[df[condition_column] == condition_value, update_column] = str(new_value)
        print(f"Updating {update_column} for {condition_value} with {new_value}")
    else:
        print(f"No matching rows found for {condition_value} in {condition_column}")
    
    # Write the updated DataFrame back to the CSV file
    df.to_csv(csv_path, index=False)
    print(f"CSV updated at {csv_path}")

In [14]:
csv_path = "C:\\Users\\ASUS\\anaconda3\\wearable-apk-manifest\\combine_filtered_cleaned.csv"
xml_directory = ".\\manifest-wearable"
apk_file_name_arr, pkg_name_arr  = read_csv_and_filter(csv_path)
print(len(apk_file_name_arr))

5285


In [15]:
for i in range(len(apk_file_name_arr)):
    print("---------------------------- Loop-"+str(i)+" ----------------------------")
    apkfile_name_new = apk_file_name_arr[i]
    pkg_name = pkg_name_arr[i]
    print("apkfile_name_new:",apkfile_name_new)
    print("pkg_name:",pkg_name)
    manifest_path = xml_directory+"\\"+str(os.path.splitext(apkfile_name_new)[0])+"-AndroidManifest.xml" 
    result = classify_app_from_manifest(manifest_path)
    print("result",result)
    update_csv_column(csv_path, "pkg_name", pkg_name, "app_group", result[0])
    update_csv_column(csv_path, "pkg_name", pkg_name, "app_group_reason", result[1][0])
    #break

---------------------------- Loop-0 ----------------------------
apkfile_name_new: Audify---Notification-Reader-4.2.0.apk
pkg_name: in.codeseed.audify
result ['Companion App', ['No <uses-library> for com.google.android.wearable found']]
Checking for rows where pkg_name == in.codeseed.audify
Found 1 matching rows
Updating app_group for in.codeseed.audify with Companion App
CSV updated at C:\Users\ASUS\anaconda3\wearable-apk-manifest\combine_filtered_cleaned.csv
Checking for rows where pkg_name == in.codeseed.audify
Found 1 matching rows
Updating app_group_reason for in.codeseed.audify with No <uses-library> for com.google.android.wearable found
CSV updated at C:\Users\ASUS\anaconda3\wearable-apk-manifest\combine_filtered_cleaned.csv
---------------------------- Loop-1 ----------------------------
apkfile_name_new: Twilight-14.0.apk
pkg_name: com.urbandroid.lux
result ['Companion App', ['No <uses-library> for com.google.android.wearable found']]
Checking for rows where pkg_name == com.ur

CSV updated at C:\Users\ASUS\anaconda3\wearable-apk-manifest\combine_filtered_cleaned.csv
---------------------------- Loop-12 ----------------------------
apkfile_name_new: Wear-Phone-Lock-for-Wear-OS-1.4.apk
pkg_name: net.ddns.axiiim.wearphonelock
result ['Companion App', ['No <uses-library> for com.google.android.wearable found']]
Checking for rows where pkg_name == net.ddns.axiiim.wearphonelock
Found 1 matching rows
Updating app_group for net.ddns.axiiim.wearphonelock with Companion App
CSV updated at C:\Users\ASUS\anaconda3\wearable-apk-manifest\combine_filtered_cleaned.csv
Checking for rows where pkg_name == net.ddns.axiiim.wearphonelock
Found 1 matching rows
Updating app_group_reason for net.ddns.axiiim.wearphonelock with No <uses-library> for com.google.android.wearable found
CSV updated at C:\Users\ASUS\anaconda3\wearable-apk-manifest\combine_filtered_cleaned.csv
---------------------------- Loop-13 ----------------------------
apkfile_name_new: Quick-System-Info-Wear-3.7.5.ap

CSV updated at C:\Users\ASUS\anaconda3\wearable-apk-manifest\combine_filtered_cleaned.csv
---------------------------- Loop-23 ----------------------------
apkfile_name_new: Shopping-List-1.0.apk
pkg_name: com.gin.shoppinglist
result ['Companion App', ['No <uses-library> for com.google.android.wearable found']]
Checking for rows where pkg_name == com.gin.shoppinglist
Found 1 matching rows
Updating app_group for com.gin.shoppinglist with Companion App
CSV updated at C:\Users\ASUS\anaconda3\wearable-apk-manifest\combine_filtered_cleaned.csv
Checking for rows where pkg_name == com.gin.shoppinglist
Found 1 matching rows
Updating app_group_reason for com.gin.shoppinglist with No <uses-library> for com.google.android.wearable found
CSV updated at C:\Users\ASUS\anaconda3\wearable-apk-manifest\combine_filtered_cleaned.csv
---------------------------- Loop-24 ----------------------------
apkfile_name_new: Smoking-Log---Stop-Smoking-6.0.11.apk
pkg_name: com.ccswe.SmokingLog
result ['Companion Ap

CSV updated at C:\Users\ASUS\anaconda3\wearable-apk-manifest\combine_filtered_cleaned.csv
---------------------------- Loop-34 ----------------------------
apkfile_name_new: Startactics_-Squadron-builder-3.63.4.apk
pkg_name: com.shinayser.xwingmanager
result ['Companion App', ['No <uses-library> for com.google.android.wearable found']]
Checking for rows where pkg_name == com.shinayser.xwingmanager
Found 1 matching rows
Updating app_group for com.shinayser.xwingmanager with Companion App
CSV updated at C:\Users\ASUS\anaconda3\wearable-apk-manifest\combine_filtered_cleaned.csv
Checking for rows where pkg_name == com.shinayser.xwingmanager
Found 1 matching rows
Updating app_group_reason for com.shinayser.xwingmanager with No <uses-library> for com.google.android.wearable found
CSV updated at C:\Users\ASUS\anaconda3\wearable-apk-manifest\combine_filtered_cleaned.csv
---------------------------- Loop-35 ----------------------------
apkfile_name_new: Salah-Wear---الصلاة-على-النبي-2.1.apk
pkg

CSV updated at C:\Users\ASUS\anaconda3\wearable-apk-manifest\combine_filtered_cleaned.csv
---------------------------- Loop-45 ----------------------------
apkfile_name_new: Chinese-Lunar-Calendar-5.8.9.apk
pkg_name: oms.mmc.fortunetelling.gmpay.almanac2
result ['Companion App', ['No <uses-library> for com.google.android.wearable found']]
Checking for rows where pkg_name == oms.mmc.fortunetelling.gmpay.almanac2
Found 1 matching rows
Updating app_group for oms.mmc.fortunetelling.gmpay.almanac2 with Companion App
CSV updated at C:\Users\ASUS\anaconda3\wearable-apk-manifest\combine_filtered_cleaned.csv
Checking for rows where pkg_name == oms.mmc.fortunetelling.gmpay.almanac2
Found 1 matching rows
Updating app_group_reason for oms.mmc.fortunetelling.gmpay.almanac2 with No <uses-library> for com.google.android.wearable found
CSV updated at C:\Users\ASUS\anaconda3\wearable-apk-manifest\combine_filtered_cleaned.csv
---------------------------- Loop-46 ----------------------------
apkfile_name

...

CSV updated at C:\Users\ASUS\anaconda3\wearable-apk-manifest\combine_filtered_cleaned.csv
---------------------------- Loop-5232 ----------------------------
apkfile_name_new: Planet-Fitness-Workouts-9.9.2.apk
pkg_name: com.planetfitness
result ['Companion App', ['No <uses-library> for com.google.android.wearable found']]
Checking for rows where pkg_name == com.planetfitness
Found 2 matching rows
Updating app_group for com.planetfitness with Companion App
CSV updated at C:\Users\ASUS\anaconda3\wearable-apk-manifest\combine_filtered_cleaned.csv
Checking for rows where pkg_name == com.planetfitness
Found 2 matching rows
Updating app_group_reason for com.planetfitness with No <uses-library> for com.google.android.wearable found
CSV updated at C:\Users\ASUS\anaconda3\wearable-apk-manifest\combine_filtered_cleaned.csv
---------------------------- Loop-5233 ----------------------------
apkfile_name_new: Galaxy-Wearable-2.2.59.24061361.apk
pkg_name: com.samsung.android.app.watchmanager
result

CSV updated at C:\Users\ASUS\anaconda3\wearable-apk-manifest\combine_filtered_cleaned.csv
---------------------------- Loop-5243 ----------------------------
apkfile_name_new: Smartphone-Link-2.11.5.apk
pkg_name: com.garmin.android.apps.phonelink
result ['Companion App', ['No <uses-library> for com.google.android.wearable found']]
Checking for rows where pkg_name == com.garmin.android.apps.phonelink
Found 1 matching rows
Updating app_group for com.garmin.android.apps.phonelink with Companion App
CSV updated at C:\Users\ASUS\anaconda3\wearable-apk-manifest\combine_filtered_cleaned.csv
Checking for rows where pkg_name == com.garmin.android.apps.phonelink
Found 1 matching rows
Updating app_group_reason for com.garmin.android.apps.phonelink with No <uses-library> for com.google.android.wearable found
CSV updated at C:\Users\ASUS\anaconda3\wearable-apk-manifest\combine_filtered_cleaned.csv
---------------------------- Loop-5244 ----------------------------
apkfile_name_new: Garmin-VIRB-4.4.

CSV updated at C:\Users\ASUS\anaconda3\wearable-apk-manifest\combine_filtered_cleaned.csv
---------------------------- Loop-5254 ----------------------------
apkfile_name_new: Huawei-Band-8-Instructions-9.apk
pkg_name: com.huaweiwatch.band8
result ['Companion App', ['No <uses-library> for com.google.android.wearable found']]
Checking for rows where pkg_name == com.huaweiwatch.band8
Found 1 matching rows
Updating app_group for com.huaweiwatch.band8 with Companion App
CSV updated at C:\Users\ASUS\anaconda3\wearable-apk-manifest\combine_filtered_cleaned.csv
Checking for rows where pkg_name == com.huaweiwatch.band8
Found 1 matching rows
Updating app_group_reason for com.huaweiwatch.band8 with No <uses-library> for com.google.android.wearable found
CSV updated at C:\Users\ASUS\anaconda3\wearable-apk-manifest\combine_filtered_cleaned.csv
---------------------------- Loop-5255 ----------------------------
apkfile_name_new: Huawei-Band-9-Fitness-Advice-1.1.1.1.apk
pkg_name: com.huaweiband9fitn

CSV updated at C:\Users\ASUS\anaconda3\wearable-apk-manifest\combine_filtered_cleaned.csv
---------------------------- Loop-5265 ----------------------------
apkfile_name_new: Mi-Band-6-Watch-Faces-1.3.1.apk
pkg_name: asn.ark.miband6
result ['Companion App', ['No <uses-library> for com.google.android.wearable found']]
Checking for rows where pkg_name == asn.ark.miband6
Found 1 matching rows
Updating app_group for asn.ark.miband6 with Companion App
CSV updated at C:\Users\ASUS\anaconda3\wearable-apk-manifest\combine_filtered_cleaned.csv
Checking for rows where pkg_name == asn.ark.miband6
Found 1 matching rows
Updating app_group_reason for asn.ark.miband6 with No <uses-library> for com.google.android.wearable found
CSV updated at C:\Users\ASUS\anaconda3\wearable-apk-manifest\combine_filtered_cleaned.csv
---------------------------- Loop-5266 ----------------------------
apkfile_name_new: Mi-Band-4-WatchFaces-7_UMP_L50.apk
pkg_name: paolo4c.mb4.watchfaces
result ['Companion App', ['No <us

CSV updated at C:\Users\ASUS\anaconda3\wearable-apk-manifest\combine_filtered_cleaned.csv
---------------------------- Loop-5276 ----------------------------
apkfile_name_new: Facebook-481.0.0.61.80.apk
pkg_name: com.facebook.katana
result ['Companion App', ['No <uses-library> for com.google.android.wearable found']]
Checking for rows where pkg_name == com.facebook.katana
Found 1 matching rows
Updating app_group for com.facebook.katana with Companion App
CSV updated at C:\Users\ASUS\anaconda3\wearable-apk-manifest\combine_filtered_cleaned.csv
Checking for rows where pkg_name == com.facebook.katana
Found 1 matching rows
Updating app_group_reason for com.facebook.katana with No <uses-library> for com.google.android.wearable found
CSV updated at C:\Users\ASUS\anaconda3\wearable-apk-manifest\combine_filtered_cleaned.csv
---------------------------- Loop-5277 ----------------------------
apkfile_name_new: Instagram-349.3.0.42.104.apk
pkg_name: com.instagram.android
result ['Companion App', 